# Transfer Learning

# Set Up

### Module Imports

In [1]:
import pandas as pd
import tensorflow as tf
from tensorflow import keras
import os
import numpy as np
from tensorflow.keras import layers, optimizers, applications, callbacks
import pathlib
import matplotlib.pyplot as plt
from ast import literal_eval
from skmultilearn.model_selection import iterative_train_test_split
from sklearn.model_selection import train_test_split
import pickle

2024-09-13 15:05:57.394476: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-09-13 15:05:59.545635: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


### Runtime Configuration
Tensorflow configuration to optimize GPU memory utilisation.<br>
https://www.tensorflow.org/guide/gpu

In [2]:
def set_memory_growth():
    gpus = tf.config.list_physical_devices('GPU')
    if gpus:
      try:
        # Currently, memory growth needs to be the same across GPUs
        for gpu in gpus:
          tf.config.experimental.set_memory_growth(gpu, True)
        logical_gpus = tf.config.list_logical_devices('GPU')
        print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
      except RuntimeError as e:
        # Memory growth must be set before GPUs have been initialized
        print(e)

def set_memory_limit(memory_limit):
    gpus = tf.config.list_physical_devices('GPU')
    if gpus:
        tf.config.set_logical_device_configuration(
            gpus[0],
            [tf.config.LogicalDeviceConfiguration(memory_limit=memory_limit)]
        )

    logical_gpus = tf.config.list_logical_devices('GPU')
    print(len(gpus), "Physical GPU,", len(logical_gpus), "Logical GPUs")

HOME = os.environ['HOME']
LOCAL = True if "ruairi" in HOME else False

if LOCAL:
    set_memory_limit(4096)
    #set_memory_growth()
    keras.mixed_precision.set_global_policy("mixed_float16")
else:
    from google.colab import drive
    drive.mount('/content/drive')

pd.set_option('display.max_columns', None)

1 Physical GPU, 1 Logical GPUs


2024-09-13 15:06:05.328541: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-13 15:06:05.663788: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-13 15:06:05.663945: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-13 15:06:05.672751: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:984] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2024-09-13 15:06:05.672968: I external/local_xla/xla/stream_executor

### Hyperparameters
These hyperparameters are declared at the start of the notebook, to be used throughout.

In [3]:
IMG_DIM = 299
IMG_SIZE = (IMG_DIM, IMG_DIM)
BATCH_SIZE = 16
AUTOTUNE = tf.data.AUTOTUNE
PATIENCE = 10
SEED = 100
TEST_VAL_SIZE = 0.2

# Where to save History and Models
history_dir = pathlib.Path("../histories/")
saved_models_dir = "../saved_models/"

***
***
***
***
***

# Model Training Hyperparameters
Set these hyperparameters prior to running the experiments.<br>
- Filtered: determines selection of stratified or unstratified dataset
- binary: determines selection of mulit-label classification parameters if True, and multi-class if false

In [4]:
filtered = True

In [5]:
# model_options = ["mobilenet", "vgg16", "inceptionv3", "inceptionresnetv2"]

In [6]:
binary = True
epochs=100
model_name = "inceptionresnetv2"
BASE_LR=0.001

***
***
***
***
***

# Data Preparation

### Dataframe Train, Val, Test Split
- Specify whether to import the previously processed and filtered dataset, or the unfiltered dataset.
- The csv is imported, the class_names are collected and the num_classes calculated.
- The dataframe is randomly split, with 80% of samples being used for training.
- If using the filtered dataset, this split is stratified by the Disease column value counts. This ensures that there is equal representation of classes in both the Train and Test/Val datasets. A random_state is specified to ensure reproducibility in this stage. This is only sued for the filtered dataset, as the unfiltered dataset has classes with only 1 sample in it, and therefore can't be stratified.
- The remaining 20% is randomly split again.  This split is not stratified, but the classes are still appropriately represented in the training set.
- The final dataframe proportions are 80-10-10%.

In [7]:
if filtered:
    # Read filtered csv file into dataframe
    csv_path = "../data/csv_files/classes_filtered.csv"
    df = pd.read_csv(csv_path)
    # Change diseaes col to be lists. Create class_names and num_classes variables
    df.Diseases = df.Diseases.apply(lambda x: literal_eval(x))
    class_names = df.columns[1:-2]
    num_classes = len(class_names)
    
    # Create X and y arrays, of filenames and class binary coding columns 
    X = df.filename.to_frame().to_numpy()
    y = df[class_names].to_numpy()

    # Iterative train test split. Predifined proportion declared in hyperparameters above.
    X_train, y_train, X_test, y_test = iterative_train_test_split(X=X, y=y, test_size=TEST_VAL_SIZE)
    # Create dataframes for all splits
    X_train = pd.DataFrame(X_train, columns = ["filename"])
    y_train = pd.DataFrame(y_train, columns = class_names)
    X_test = pd.DataFrame(X_test, columns = ["filename"])
    y_test = pd.DataFrame(y_test, columns = class_names)
    # Merge dataframes into train and test
    train_df = X_train.merge(y_train, left_index=True, right_index=True)
    test_df = X_test.merge(y_test, left_index=True, right_index=True)

    # Repeat above process, splitting the test set into validation and test, 50/50 split.
    X = test_df.filename.to_frame().to_numpy()
    y = test_df[class_names].to_numpy()

    X_val, y_val, X_test, y_test = iterative_train_test_split(X=X, y=y, test_size=0.5)
    X_val = pd.DataFrame(X_val, columns = ["filename"])
    y_val = pd.DataFrame(y_val, columns = class_names)
    X_test = pd.DataFrame(X_test, columns = ["filename"])
    y_test = pd.DataFrame(y_test, columns = class_names)
    
    val_df = X_val.merge(y_val, left_index=True, right_index=True)
    test_df = X_test.merge(y_test, left_index=True, right_index=True)

In [8]:
if not filtered:
    # Read unfiltered csv file into dataframe
    csv_path = "../data/csv_files/classes_processed.csv"
    df = pd.read_csv(csv_path)
    # Change diseaes col to be lists. Create class_names and num_classes variables
    df.Diseases = df.Diseases.apply(lambda x: literal_eval(x))
    class_names = df.columns[1:-2]
    num_classes = len(class_names)
    # Train test split, with no stratification
    train_df, test_df = train_test_split(df, test_size=TEST_VAL_SIZE, random_state=SEED)
    val_df, test_df = train_test_split(test_df, test_size=0.5, random_state=SEED)

In [9]:
print(f"Filtered: {filtered}")
print(f"CSV path: {csv_path}")
print(f"Dataframe Shape: {df.shape}")
print(f"Class Names: {list(class_names)}")
print(f"Num Classes: {num_classes}")
print("Dataset shapes:")
print(f"Train DF: {train_df.shape}")
print(f"Val DF: {val_df.shape}")
print(f"Test DF: {test_df.shape}")
total_samples = len(train_df) + len(val_df) + len(test_df)
print(f"Total Samples: {total_samples}")
display(df.head(3))

Filtered: True
CSV path: ../data/csv_files/classes_filtered.csv
Dataframe Shape: (5154, 28)
Class Names: ['Cassava Bacterial Blight', 'Cassava Brown Leaf Spot', 'Cassava Healthy', 'Cassava Mosaic', 'Cassava Root Rot', 'Corn Brown Spots', 'Corn Chlorotic Leaf Spot', 'Corn Gray leaf spot', 'Corn Healthy', 'Corn Insects Damages', 'Corn Mildew', 'Corn Purple Discoloration', 'Corn Smut', 'Corn Streak', 'Corn Stripe', 'Corn Violet Decoloration', 'Corn Yellow Spots', 'Corn Yellowing', 'Corn leaf blight', 'Corn rust leaf', 'Tomato Brown Spots', 'Tomato blight leaf', 'Tomato healthy', 'Tomato leaf mosaic virus', 'Tomato leaf yellow virus']
Num Classes: 25
Dataset shapes:
Train DF: (4125, 26)
Val DF: (513, 26)
Test DF: (516, 26)
Total Samples: 5154


filename  \
0  Charbon_de_mais-1-_jpg.rf.d83e40544e3be2dac4fd...   
1  Charbon_de_mais-2-_jpg.rf.e2c36854e8f83c0f5cdd...   
2  Charbon_de_mais-3-_jpg.rf.7779b177d76937957b47...   

   Cassava Bacterial Blight  Cassava Brown Leaf Spot  Cassava Healthy  \
0                         0                        0                0   
1                         0                        0                0   
2                         0                        0                0   

   Cassava Mosaic  Cassava Root Rot  Corn Brown Spots  \
0               0                 0                 0   
1               0                 0                 0   
2               0                 0                 0   

   Corn Chlorotic Leaf Spot  Corn Gray leaf spot  Corn Healthy  \
0                         0                    0             0   
1                         0                    0             0   
2                         0                    0             0   

   Corn Insects Damages  Corn Mildew  Corn Purple Discoloration  Corn Smut  \
0                     0            0                          0          1   
1                     0            0                          0          1   
2                     0            0                          0          1   

   Corn Streak  Corn Stripe  Corn Violet Decoloration  Corn Yellow Spots  \
0            0            0                         0                  0   
1            0            0                         0                  0   
2            0            0                         0                  0   

   Corn Yellowing  Corn leaf blight  Corn rust leaf  Tomato Brown Spots  \
0               0                 0               0                   0   
1               0                 0               0                   0   
2               0                 0               0                   0   

   Tomato blight leaf  Tomato healthy  Tomato leaf mosaic virus  \
0                   0               0                         0   
1                   0               0                         0   
2                   0               0                         0   

   Tomato leaf yellow virus     Diseases     Crops  
0                         0  [Corn Smut]  ['Corn']  
1                         0  [Corn Smut]  ['Corn']  
2                         0  [Corn Smut]  ['Corn']

In [10]:
# Print random row where the sample contains more than one label
multilabel_samples = df[df.apply(lambda row: len(row.Diseases) > 1, axis=1)]
random_sample = multilabel_samples.sample(1)
print("Random Sample with Multiple Labels")
random_sample

Random Sample with Multiple Labels


filename  \
361  IMG_20221118_081618_338_jpg.rf.3f511f16b75aca1...   

     Cassava Bacterial Blight  Cassava Brown Leaf Spot  Cassava Healthy  \
361                         0                        0                0   

     Cassava Mosaic  Cassava Root Rot  Corn Brown Spots  \
361               0                 0                 0   

     Corn Chlorotic Leaf Spot  Corn Gray leaf spot  Corn Healthy  \
361                         0                    0             0   

     Corn Insects Damages  Corn Mildew  Corn Purple Discoloration  Corn Smut  \
361                     0            0                          0          0   

     Corn Streak  Corn Stripe  Corn Violet Decoloration  Corn Yellow Spots  \
361            0            0                         0                  0   

     Corn Yellowing  Corn leaf blight  Corn rust leaf  Tomato Brown Spots  \
361               0                 0               0                   0   

     Tomato blight leaf  Tomato healthy  Tomato leaf mosaic virus  \
361                   1               1                         0   

     Tomato leaf yellow virus                              Diseases  \
361                         0  [Tomato blight leaf, Tomato healthy]   

          Crops  
361  ['Tomato']

***
***
***

### Dataset Creation
- The datasets of filenames and labels are then created using the split dataframes above.
- They are shuffled fully and then the filenames are processed into image pixels.
##### Inspect
- Dataset sizes are printed, element spec is inspected, and a sample of a image pixel tensor and it's labels are printed.
##### Configure Datasets
- The datasets are then configured for performance, using caching, shuffling, batching and prefetch, to optimize the tf.data pipeline.<br>
- https://www.tensorflow.org/guide/data_performance<br>

### Functions
Functions to be used in the processing of data below. Some are custom made, others are taken from tutorials.<br>

- dataset_from_dataframe: Creates a TF dataset of filenames and disease labels from a Pandas DataFrame, using the specified disease label columns<br>
- decode_img: Converts an image filepath name of a jpeg file to a tensor of pixels. (https://www.tensorflow.org/tutorials/load_data/images#using_tfdata_for_finer_control)<br>
- process_dataset: parent function to process image file and return dataset of pixels and labels.<br>
- configure_dataset_for_performance: uses caching, shuffling, batchin and prefetching to optimize the tf.data pipeline.https://www.tensorflow.org/guide/data_performance<br>
- drop_remainder = True oto allow for uniform batch sizes and XLA.

In [11]:
# Converts dataframe to dataset
def dataset_from_dataframe(dataframe, class_names):
    # Gets X = filename
    img = dataframe.filename
    # Gets y = binary encoded class labels
    labels = dataframe[class_names]
    # Creates dataset of filename and binary encoded labels
    return tf.data.Dataset.from_tensor_slices((img, labels))

# Converts filename string to tensor of pixels
def decode_img(filename, img_size):
    # Declare image ddirectory and filepath of image
    img_dir = "../data/images/"
    filepath = img_dir + filename
    # Read the file, convert jpeg to tensor, resize image tensor.
    img = tf.io.read_file(filepath)
    img = tf.io.decode_jpeg(img, channels=3)
    img = tf.image.resize(img, img_size)
    return img

# Parent function to return dataset of image pixels and labels, optionally return filename string
def process_dataset(filename, labels, img_size=IMG_SIZE, return_filenames=False):
    # Return image pixel tensor
    img = decode_img(filename, img_size=img_size)
    # optional to return filenames with image and labels.  Used for verification
    if return_filenames:
        return img, labels, filename
    else:
        return img, labels

# Optimize performance of tf dataset pipeline
def configure_dataset_for_performance(dataset, shuffle=False, batch_size=BATCH_SIZE):
    dataset = dataset.cache()
    if shuffle:
        dataset = dataset.shuffle(buffer_size=dataset.cardinality(), reshuffle_each_iteration=True)
    dataset = dataset.batch(batch_size=batch_size, num_parallel_calls=AUTOTUNE)
    dataset = dataset.prefetch(buffer_size=AUTOTUNE)
    return dataset

In [12]:
# Create datasets which returns filename and binary encoded labels
train_ds1 = dataset_from_dataframe(train_df, class_names).shuffle(len(train_df))
val_ds1 = dataset_from_dataframe(val_df, class_names).shuffle(len(val_df))
test_ds1 = dataset_from_dataframe(test_df, class_names).shuffle(len(test_df))

# Convert filename into image pixels array
train_ds1 = train_ds1.map(lambda x,y:process_dataset(x, y, return_filenames=False))
val_ds1 = val_ds1.map(lambda x,y:process_dataset(x, y, return_filenames=False))
test_ds1 = test_ds1.map(lambda x,y:process_dataset(x, y, return_filenames=False))

print(f"Total no.: samples: {len(df)}")
print(f"Training Samples: {len(train_ds1)}")
print(f"Validation Samples: {len(val_ds1)}")
print(f"Testing Samples: {len(test_ds1)}")
print()
for i in train_ds1.element_spec:
    print(i)

for x, y in train_ds1.take(1):
    print(x)
    print(y)

# Optimize tf dataset
train_ds1 = configure_dataset_for_performance(train_ds1, shuffle=True)
val_ds1 = configure_dataset_for_performance(val_ds1)
test_ds1 = configure_dataset_for_performance(test_ds1)

Total no.: samples: 5154
Training Samples: 4125
Validation Samples: 513
Testing Samples: 516

TensorSpec(shape=(299, 299, 3), dtype=tf.float32, name=None)
TensorSpec(shape=(25,), dtype=tf.int64, name=None)
tf.Tensor(
[[[6.23029289e+01 5.73029289e+01 5.43029289e+01]
  [8.62391357e+01 8.07826080e+01 7.77826080e+01]
  [8.98190002e+01 8.18190002e+01 7.88190002e+01]
  ...
  [9.67754974e+01 1.45601669e+02 0.00000000e+00]
  [9.30874023e+01 1.45391602e+02 0.00000000e+00]
  [9.75654297e+01 1.50565430e+02 0.00000000e+00]]

 [[4.87173920e+01 4.37173920e+01 4.07173920e+01]
  [6.32826157e+01 5.84347916e+01 5.54347916e+01]
  [5.21739159e+01 4.81739159e+01 4.51739159e+01]
  ...
  [9.74126358e+01 1.45412643e+02 1.52661711e-01]
  [9.59779663e+01 1.45921753e+02 0.00000000e+00]
  [9.52650833e+01 1.48265076e+02 0.00000000e+00]]

 [[5.40000000e+01 4.80000000e+01 5.00000000e+01]
  [4.55642700e+01 3.95642700e+01 3.95642700e+01]
  [2.27173920e+01 1.77173920e+01 1.47173920e+01]
  ...
  [9.84130859e+01 1.464130

2024-09-13 15:06:18.119969: W tensorflow/core/framework/local_rendezvous.cc:404] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


***
***
***

# Model Functions
The following functions are to build the model training pipeline specified below.
- get_hyprerparams: returns the relevant loss function, metrics, and activation function for either Binary classification or Softmax.
- get_freeze_at_layer: returns the layer at which to freeze the base model.
- freeze_mode: freezes the base model at the predefined layer.
- get_base_model: returns the specified base model.
- get_preprocessing: returns the relevant preprocessing module for the base model.
- build_model: parent function to build the specified model.  Includes preprocessing if required, a 20% Dropout layer before GlobalAveragePooling, and an extra Dense Layer with 128 units before the classifier layer using the relevant chosen activation function.
- apply_resize: resizes the input to match the default size of the model being used.
- show_all_model_info: displays info such as model.summary(), activation functions, loss functions, metrics, model layers, and trainable layers.  Used to verify that the model is correct before training.

In [1]:
# Returns the appropriate loss function, metrics, and activation function depending on whether the task if binary (multilabel) or not
def get_hyperparams(binary=False):
    loss = "binary_crossentropy" if binary else "categorical_crossentropy"
    metrics = ["binary_accuracy"] if binary else ["categorical_accuracy"]
    # f1 score uses weighted macro average which is more suitable for imbalanced datasets
    # Also f1 score per class added
    f1_score_weighted = keras.metrics.F1Score(average="weighted", threshold=0.5 if binary else None, name="f1_score_weighted", dtype=None)
    f1_score_per_class = keras.metrics.F1Score(average=None, threshold=0.5 if binary else None, name="f1_score_per_class", dtype=None)
    metrics.append(f1_score_weighted)
    metrics.append(f1_score_per_class)
    # Sigmoid for multilabel classification, softmax for multiclass classification
    activation = "sigmoid" if binary else "softmax"
    return loss, metrics, activation

# Returns the number at which to freeze the model fro fine tuning
def get_freeze_at_layer(model_name):
    model_name = model_name.lower()
    if "mobilenet" in model_name:
        # 120 used in FP
        # last block 143
        return 120
    if "vgg16" in model_name:
        # 14 used in FP
        # last layer 17
        return 14
    if "inceptionv3" in model_name:
        # 172 used in FP
        # last block 279
        return 172
    if "inceptionresnetv2" in model_name:
        # 516 used in FP
        # 761 last block
        return 516

# Function to freeze the given base model at the desired layer number
def freeze_model(base_model, freeze_at):
    # freezes initial layers
    for layer in base_model.layers[:freeze_at]:
        layer.trainable=False
    # unfreezes later
    for layer in base_model.layers[freeze_at:]:
        layer.trainable = True

# Returns the specified base model with default input size, and trainable set to false
def get_base_model(model_name, include_top=False):
    model_name = model_name.lower()
    if "mobilenet" in model_name:
        base_model = applications.MobileNetV2(include_top=include_top, input_shape=(224, 224, 3) )
    elif "vgg16" in model_name:
        base_model = applications.VGG16(include_top=include_top, input_shape=(224, 224, 3) )
    elif "inceptionv3" in model_name:
        base_model = applications.InceptionV3(include_top=include_top, input_shape=(299,299,3))
    elif "inceptionresnetv2" in model_name:
        base_model = applications.InceptionResNetV2(include_top=include_top, input_shape=(299,299,3))
    # Change base models name to easier version
    base_model.name = model_name
    base_model.trainable = False
    return base_model

# Gets the required preprocessing layer for the relevant base model
def get_preprocessing(model_name):
    model_name = model_name.lower()
    if "mobilenet" in model_name:
        return applications.mobilenet_v2.preprocess_input
    elif "vgg16" in model_name:
        return applications.vgg16.preprocess_input
    elif "inceptionv3" in model_name:
        return applications.inception_v3.preprocess_input
    elif "inceptionresnetv2" in model_name:
        return applications.inception_resnet_v2.preprocess_input

def get_pre_classifier_layers(model_name):
    model_name = model_name.lower()
    if model_name in ["mobilenet", "inceptionv3", "inceptionresnetv2"]:
        return keras.Sequential([layers.GlobalAveragePooling2D()])
    if model_name in ["vgg16"]:
        return keras.Sequential([layers.GlobalAveragePooling2D(), layers.Dense(1024, activation="relu"), layers.Dense(1024, activation="relu") ])
        
# Parnet function to return the build model.
def build_model(base_model, preprocessing, activation):
    # set inputs to the default input shape of the base model
    inputs = keras.Input(base_model.input_shape[1:])
    # apply base model's preprocessing to the inputs
    x = preprocessing(inputs)
    # apply the base model to x
    # Set training = False so that Batch Normalization does not update values
    x = base_model(x, training=False)

    # Add extra layers after Base and model and Pre classifier.
    # Includes Global Average Pooling and Dense layers, depending on model
    pre_classifier_layers = get_pre_classifier_layers(base_model.name)
    x = pre_classifier_layers(x)

    # apply dropout
    x = layers.Dropout(0.2)(x)
    
    # Final classifier dense layer, using the number of classes as the number of units.
    # The activation function is specified as Sigmoid or Softmax as before
    outputs = layers.Dense(num_classes, activation=activation, name="classifier_layer")(x)

    # set the model name to be the same as the altered base model name
    model_name = base_model.name
    # Add a suffix to the name, depending on model type
    model_name += "_binary" if binary else "_softmax"

    # declare and return model
    model = keras.Model(inputs, outputs, name=model_name)
    return model

# Function to appropriately resize the image tensor for the model
# Takes a specified image dimension param
def apply_resize(x, img_dim):
    return layers.Resizing(img_dim, img_dim)(x)

# Displays all model info
def show_all_model_info(model):
    # gets just the base model layers
    base_model = model.get_layer(index=1)
    # gets the compile configuration 
    config = model.get_compile_config()
    # optiizer info
    opt = config["optimizer"]["config"]
    print(f"Optimizer Name: {opt['name']}, Learning Rate: {np.round(opt['learning_rate'], 6)} ")
    print(f"Loss: {model.loss}")
    # metrics used
    print(f"Metrics: {config['metrics']}")
    # get the name of the activation function in the classifier layer
    classifier_activation = model.get_layer(name="classifier_layer").activation.__name__
    print(f"Classifier Activation: {classifier_activation}")

    # Prints summary of whole model
    print(model.summary())
    # prints summary from the start of the base model layers onwards.  Shows all nested layers, displays if layers are trainable
    print(model.summary(layer_range=(base_model.name, 
                                     model.get_layer(index=-1).name),
                        expand_nested=True, show_trainable=True))

    # Prints all the layers and their index number of just the base model
    for i, layer in enumerate(base_model.layers):
        print(i, layer)

    # attempts to plot the model in image format
    try:
        display(keras.utils.plot_model(base_model, expand_nested=True, dpi=50, show_layer_names=True) )
    except:
        print("unable to display model")
    # closes the pyplot figure
    plt.close()

***
***
***

# Model Training
https://www.tensorflow.org/tutorials/images/transfer_learning
- The process below is to be run for each type of Model.
- The set up variables below can be changed as needed.
- Binary: boolean variable to specify whether to use hyperparameters for Binary Classification, or False for SoftMax classification.
- model_name: specify which model to run.
- 4 models are trained, each on the 2 options for Binary, resulting in 8 sets of histories to analyse.
- models: MobileNetV2, VGG16, InceptionV3, InceptionResNetV2.

### Set up Variables
The following cell sets the variables to be used in the running of the model training below.
- binary: if True, useshyperparameters suitable for Binary Classification. If False, uses hyperparameters for SoftMax Classification,
- epochs: max epochs to train model for.
- model_name: provided to functions above, to obtain the correct model, preprocessing layers and layer to freeze at.
- BASE_LR: the base learning rate, same as the Keras default for Adam optimizer.  Specified so that a smaller learning rate can be specified for fine tuning stage.

### 1. Top Classifier
- Get the base model and relevant preprocessing layer.
- Get the relevant metrics for Binary/Softmax Classification.
- Reshape datasets to model's default size specifications.
- build model using prevous function.  Includes 20% Dropout before GlobalNMaxPooling, and a Dense layer of 128 units before the final classifier Dense Layer.
- Compile model using relevant hyperparameters for the type of classification.
- Callbacks: EarlyStopping used to return model at best epoch. ModelCheckpoint used to save model at best epoch.

The model information is then inspected and verifie to be correct before training.

In [14]:
# Gets the base model, hyperparams, and preprocessing based on the declared model name near the beginning of the notebook
base_model = get_base_model(model_name, include_top=False)
for layer in base_model.layers:
    if isinstance(layer, layers.BatchNormalization):
        layer.trainable = False
        
loss, metrics, activation = get_hyperparams(binary=binary)
preprocessing = get_preprocessing(model_name)
print(base_model)
# Sets the image dimension to the default of the specified model and resizes all datasets
img_dim = base_model.input_shape[1]
train_ds = train_ds1.map(lambda x,y: (apply_resize(x, img_dim), y), num_parallel_calls=AUTOTUNE)
val_ds = val_ds1.map(lambda x,y: (apply_resize(x, img_dim), y), num_parallel_calls=AUTOTUNE)
test_ds = test_ds1.map(lambda x,y: (apply_resize(x, img_dim), y), num_parallel_calls=AUTOTUNE)

# Print the element specs of each dataset
print("Train Shape")
print(train_ds.element_spec)
print("Val Shape")
print(val_ds.element_spec)
print("Test Shape")
print(test_ds.element_spec)
print()

# Build the model from the previously defined function.  Pass the preprocessing mode and the activation function
model = build_model(base_model, preprocessing=preprocessing, activation=activation)

# Compile the model.  Add the loss function.  Use the base learning rate specified at the start of the notebook.
# Add the appropriate metrics for the classification problem.
model.compile(
    loss=loss,
    optimizer = optimizers.Adam(learning_rate=BASE_LR),
    metrics=metrics
)
# Add suffix to name if dataset is the filtered/stratified version                           
model.name += "_unfiltered" if not filtered else ""


# Declare callbacks.
# Early stopping: Patience declared earlier. Restore mdoel to best weights, no baseline value for initial training.
# Model Checkpoint: specifiy filepath, save only the best model, onitor validation loss, no initial threshold to beat
cbs = [callbacks.EarlyStopping(patience=PATIENCE, restore_best_weights=True, baseline=None, verbose=1),
       callbacks.ModelCheckpoint(filepath=f"{saved_models_dir}{model.name}.keras", save_best_only=True, monitor="val_loss", verbose=1, initial_value_threshold=None)]

# Display all model info using the function created above
show_all_model_info(model)

<Functional name=inceptionresnetv2, built=True>
Train Shape
(TensorSpec(shape=(None, 299, 299, 3), dtype=tf.float16, name=None), TensorSpec(shape=(None, 25), dtype=tf.int64, name=None))
Val Shape
(TensorSpec(shape=(None, 299, 299, 3), dtype=tf.float16, name=None), TensorSpec(shape=(None, 25), dtype=tf.int64, name=None))
Test Shape
(TensorSpec(shape=(None, 299, 299, 3), dtype=tf.float16, name=None), TensorSpec(shape=(None, 25), dtype=tf.int64, name=None))

Optimizer Name: adam, Learning Rate: 0.001 
Loss: binary_crossentropy
Metrics: ['binary_accuracy', {'module': 'keras.metrics', 'class_name': 'F1Score', 'config': {'name': 'f1_score_weighted', 'dtype': 'float32', 'average': 'weighted', 'threshold': 0.5}, 'registered_name': None}, {'module': 'keras.metrics', 'class_name': 'F1Score', 'config': {'name': 'f1_score_per_class', 'dtype': 'float32', 'average': None, 'threshold': 0.5}, 'registered_name': None}]
Classifier Activation: sigmoid


Model: "inceptionresnetv2_binary"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_1 (InputLayer)      │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ true_divide (TrueDivide)        │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ subtract (Subtract)             │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ inceptionresnetv2 (Functional)  │ (None, 8, 8, 1536)     │    54,336,736 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ sequential (Sequential)         │ (None, 1536)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 1536)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ classifier_layer (Dense)        │ (None, 25)             │        38,425 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 54,375,161 (207.42 MB)

 Trainable params: 38,425 (150.10 KB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ inceptionresnetv2           │ (None, 8, 8, 1536)    │ 54,336,736 │   N   │
│ (Functional)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ input_layer            │ (None, 299, 299, 3)   │          0 │   -   │
│ (InputLayer)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d (Conv2D)        │ (None, 149, 149, 32)  │        864 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization    │ (None, 149, 149, 32)  │         96 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation             │ (None, 149, 149, 32)  │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_1 (Conv2D)      │ (None, 147, 147, 32)  │      9,216 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_1  │ (None, 147, 147, 32)  │         96 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_1           │ (None, 147, 147, 32)  │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_2 (Conv2D)      │ (None, 147, 147, 64)  │     18,432 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_2  │ (None, 147, 147, 64)  │        192 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_2           │ (None, 147, 147, 64)  │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ max_pooling2d          │ (None, 73, 73, 64)    │          0 │   -   │
│ (MaxPooling2D)              │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_3 (Conv2D)      │ (None, 73, 73, 80)    │      5,120 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_3  │ (None, 73, 73, 80)    │        240 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_3           │ (None, 73, 73, 80)    │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_4 (Conv2D)      │ (None, 71, 71, 192)   │    138,240 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_4  │ (None, 71, 71, 192)   │        576 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_4           │ (None, 71, 71, 192)   │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼─────

 Total params: 54,375,161 (207.42 MB)

 Trainable params: 38,425 (150.10 KB)

 Non-trainable params: 54,336,736 (207.28 MB)

None
0 <InputLayer name=input_layer, built=True>
1 <Conv2D name=conv2d, built=True>
2 <BatchNormalization name=batch_normalization, built=True>
3 <Activation name=activation, built=True>
4 <Conv2D name=conv2d_1, built=True>
5 <BatchNormalization name=batch_normalization_1, built=True>
6 <Activation name=activation_1, built=True>
7 <Conv2D name=conv2d_2, built=True>
8 <BatchNormalization name=batch_normalization_2, built=True>
9 <Activation name=activation_2, built=True>
10 <MaxPooling2D name=max_pooling2d, built=True>
11 <Conv2D name=conv2d_3, built=True>
12 <BatchNormalization name=batch_normalization_3, built=True>
13 <Activation name=activation_3, built=True>
14 <Conv2D name=conv2d_4, built=True>
15 <BatchNormalization name=batch_normalization_4, built=True>
16 <Activation name=activation_4, built=True>
17 <MaxPooling2D name=max_pooling2d_1, built=True>
18 <Conv2D name=conv2d_8, built=True>
19 <BatchNormalization name=batch_normalization_8, built=True>
20 <Activation name=activation

##### Train top classifier layers, with frozen base model

In [15]:
history_clf = model.fit(train_ds, validation_data=val_ds, epochs=epochs, callbacks=cbs)

Epoch 1/100


2024-09-06 20:51:26.250812: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:450] ShuffleDatasetV3:12: Filling up shuffle buffer (this may take a while): 1837 of 4125
2024-09-06 20:51:36.267148: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:450] ShuffleDatasetV3:12: Filling up shuffle buffer (this may take a while): 3706 of 4125
2024-09-06 20:51:38.513701: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:480] Shuffle buffer filled.
I0000 00:00:1725652298.641081   84438 service.cc:145] XLA service 0x7fccf8142aa0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1725652298.641156   84438 service.cc:153]   StreamExecutor device (0): NVIDIA GeForce RTX 3050 Laptop GPU, Compute Capability 8.6
2024-09-06 20:51:39.128353: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2024-09-06 20:51:41.287570: I external/local_xla/xla/

258/258 ━━━━━━━━━━━━━━━━━━━━ 0s 129ms/step - binary_accuracy: 0.9504 - f1_score_per_class: 0.0766 - f1_score_weighted: 0.3296 - loss: 0.1442
Epoch 1: val_loss improved from inf to 0.08346, saving model to ../saved_models/inceptionresnetv2_binary.keras
258/258 ━━━━━━━━━━━━━━━━━━━━ 111s 236ms/step - binary_accuracy: 0.9504 - f1_score_per_class: 0.0767 - f1_score_weighted: 0.3300 - loss: 0.1441 - val_binary_accuracy: 0.9716 - val_f1_score_per_class: 0.1331 - val_f1_score_weighted: 0.5092 - val_loss: 0.0835
Epoch 2/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step - binary_accuracy: 0.9736 - f1_score_per_class: 0.1619 - f1_score_weighted: 0.5436 - loss: 0.0730
Epoch 2: val_loss improved from 0.08346 to 0.07527, saving model to ../saved_models/inceptionresnetv2_binary.keras
258/258 ━━━━━━━━━━━━━━━━━━━━ 24s 90ms/step - binary_accuracy: 0.9736 - f1_score_per_class: 0.1620 - f1_score_weighted: 0.5437 - loss: 0.0730 - val_binary_accuracy: 0.9718 - val_f1_score_per_class: 0.1590 - val_f1_score_weigh

### Fine Tuning
- Classifier training History is saved to dataframe.
- Best epoch is identified as having the lowest value for "val_loss".
- The dataframe is then saved only up to this best epoch.
- best_loss is saved and used as the threshold to beat for the ModelCheckpoint to save the model.
- best_epoch is saved, as this will be the "initial_epoch" for fine tuning the model.
- The model is frozen up until the specified layer, and unfrozen after that.
- The model is compiled withthe same metrics as previous, except for a smaller learning rate, 10% of what was used in the first stage.
- Same callbacks are used, except starting at the specified epoch, and monitoring compared to the best_val_loss baseline.
- Model info is inspected again before training.

In [16]:
history_clf_df = pd.DataFrame(history_clf.history)
history_clf_df["type"] = "CLF"
history_clf_df["epoch"] = np.array(history_clf.epoch)
best_epoch = history_clf_df.epoch[history_clf_df.val_loss == history_clf_df.val_loss.min()].values[0]
history_clf_df = history_clf_df.iloc[:best_epoch+1, :]
best_val_loss = history_clf_df.tail(1).val_loss.values[0]
initial_epoch = len(history_clf_df)

In [17]:
freeze_at = get_freeze_at_layer(model.name)
freeze_model(base_model, freeze_at)

for layer in base_model.layers:
    if isinstance(layer, layers.BatchNormalization):
        layer.trainable = False
        
model.compile(
    loss=loss,
    optimizer = optimizers.Adam(learning_rate=BASE_LR/10),
    metrics=metrics
)

cbs = [callbacks.EarlyStopping(patience=PATIENCE, restore_best_weights=True, baseline=best_val_loss, verbose=1),
       callbacks.ModelCheckpoint(filepath=f"{saved_models_dir}{model.name}.keras", save_best_only=True, monitor="val_loss", verbose=1, initial_value_threshold=best_val_loss)]

show_all_model_info(model)

Optimizer Name: adam, Learning Rate: 0.0001 
Loss: binary_crossentropy
Metrics: ['binary_accuracy', {'module': 'keras.metrics', 'class_name': 'F1Score', 'config': {'name': 'f1_score_weighted', 'dtype': 'float32', 'average': 'weighted', 'threshold': 0.5}, 'registered_name': None}, {'module': 'keras.metrics', 'class_name': 'F1Score', 'config': {'name': 'f1_score_per_class', 'dtype': 'float32', 'average': None, 'threshold': 0.5}, 'registered_name': None}]
Classifier Activation: sigmoid


Model: "inceptionresnetv2_binary"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_1 (InputLayer)      │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ true_divide (TrueDivide)        │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ subtract (Subtract)             │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ inceptionresnetv2 (Functional)  │ (None, 8, 8, 1536)     │    54,336,736 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ sequential (Sequential)         │ (None, 1536)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 1536)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ classifier_layer (Dense)        │ (None, 25)             │        38,425 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 54,375,161 (207.42 MB)

 Trainable params: 32,935,065 (125.64 MB)

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ inceptionresnetv2           │ (None, 8, 8, 1536)    │ 54,336,736 │   N   │
│ (Functional)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ input_layer            │ (None, 299, 299, 3)   │          0 │   -   │
│ (InputLayer)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d (Conv2D)        │ (None, 149, 149, 32)  │        864 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization    │ (None, 149, 149, 32)  │         96 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation             │ (None, 149, 149, 32)  │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_1 (Conv2D)      │ (None, 147, 147, 32)  │      9,216 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_1  │ (None, 147, 147, 32)  │         96 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_1           │ (None, 147, 147, 32)  │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_2 (Conv2D)      │ (None, 147, 147, 64)  │     18,432 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_2  │ (None, 147, 147, 64)  │        192 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_2           │ (None, 147, 147, 64)  │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ max_pooling2d          │ (None, 73, 73, 64)    │          0 │   -   │
│ (MaxPooling2D)              │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_3 (Conv2D)      │ (None, 73, 73, 80)    │      5,120 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_3  │ (None, 73, 73, 80)    │        240 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_3           │ (None, 73, 73, 80)    │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ conv2d_4 (Conv2D)      │ (None, 71, 71, 192)   │    138,240 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ batch_normalization_4  │ (None, 71, 71, 192)   │        576 │   N   │
│ (BatchNormalization)        │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│    └ activation_4           │ (None, 71, 71, 192)   │          0 │   -   │
│ (Activation)                │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼─────

 Total params: 54,375,161 (207.42 MB)

 Trainable params: 32,935,065 (125.64 MB)

 Non-trainable params: 21,440,096 (81.79 MB)

None
0 <InputLayer name=input_layer, built=True>
1 <Conv2D name=conv2d, built=True>
2 <BatchNormalization name=batch_normalization, built=True>
3 <Activation name=activation, built=True>
4 <Conv2D name=conv2d_1, built=True>
5 <BatchNormalization name=batch_normalization_1, built=True>
6 <Activation name=activation_1, built=True>
7 <Conv2D name=conv2d_2, built=True>
8 <BatchNormalization name=batch_normalization_2, built=True>
9 <Activation name=activation_2, built=True>
10 <MaxPooling2D name=max_pooling2d, built=True>
11 <Conv2D name=conv2d_3, built=True>
12 <BatchNormalization name=batch_normalization_3, built=True>
13 <Activation name=activation_3, built=True>
14 <Conv2D name=conv2d_4, built=True>
15 <BatchNormalization name=batch_normalization_4, built=True>
16 <Activation name=activation_4, built=True>
17 <MaxPooling2D name=max_pooling2d_1, built=True>
18 <Conv2D name=conv2d_8, built=True>
19 <BatchNormalization name=batch_normalization_8, built=True>
20 <Activation name=activation

##### Model Fine Tuning

In [18]:
history_ft = model.fit(train_ds, validation_data=val_ds, epochs=epochs, callbacks=cbs, initial_epoch=initial_epoch)

Epoch 33/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - binary_accuracy: 0.9812 - f1_score_per_class: 0.5782 - f1_score_weighted: 0.7400 - loss: 0.0567
Epoch 33: val_loss improved from 0.05471 to 0.04804, saving model to ../saved_models/inceptionresnetv2_binary.keras
258/258 ━━━━━━━━━━━━━━━━━━━━ 127s 296ms/step - binary_accuracy: 0.9812 - f1_score_per_class: 0.5783 - f1_score_weighted: 0.7401 - loss: 0.0567 - val_binary_accuracy: 0.9809 - val_f1_score_per_class: 0.5006 - val_f1_score_weighted: 0.7130 - val_loss: 0.0480
Epoch 34/100
258/258 ━━━━━━━━━━━━━━━━━━━━ 0s 122ms/step - binary_accuracy: 0.9913 - f1_score_per_class: 0.7890 - f1_score_weighted: 0.8865 - loss: 0.0234
Epoch 34: val_loss improved from 0.04804 to 0.04057, saving model to ../saved_models/inceptionresnetv2_binary.keras
258/258 ━━━━━━━━━━━━━━━━━━━━ 40s 153ms/step - binary_accuracy: 0.9913 - f1_score_per_class: 0.7891 - f1_score_weighted: 0.8865 - loss: 0.0234 - val_binary_accuracy: 0.9846 - val_f1_score_per_class: 0.530

### Concat and save History
The history from the classifier training and Fine Tuning training are concatenated and saved to a csv file for furhter analysis.

In [19]:
history_ft_df = pd.DataFrame(history_ft.history)
history_ft_df["epoch"] = history_ft.epoch
history_ft_df["type"] = "FT"

combined_history = pd.concat([history_clf_df, history_ft_df]).reset_index(drop=True)
save_path = f"../histories/{model.name}.csv"
combined_history.to_csv(save_path, index=False)

In [20]:
combined_history

binary_accuracy                                 f1_score_per_class  \
0          0.965740  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...   
1          0.974352  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...   
2          0.976698  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...   
3          0.977755  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...   
4          0.978996  (tf.Tensor(0.28571427, shape=(), dtype=float32...   
5          0.980073  (tf.Tensor(0.28571427, shape=(), dtype=float32...   
6          0.979976  (tf.Tensor(0.19047616, shape=(), dtype=float32...   
7          0.981294  (tf.Tensor(0.4347826, shape=(), dtype=float32)...   
8          0.981479  (tf.Tensor(0.19999997, shape=(), dtype=float32...   
9          0.982264  (tf.Tensor(0.36363634, shape=(), dtype=float32...   
10         0.982982  (tf.Tensor(0.36363634, shape=(), dtype=float32...   
11         0.983312  (tf.Tensor(0.36363634, shape=(), dtype=float32...   
12         0.983447  (tf.Tensor(0.4347826, shape=(), dtype=float32)...   
13         0.983894  (tf.Tensor(0.49999997, shape=(), dtype=float32...   
14         0.984339  (tf.Tensor(0.5384615, shape=(), dtype=float32)...   
15         0.984077  (tf.Tensor(0.6666666, shape=(), dtype=float32)...   
16         0.984601  (tf.Tensor(0.59259254, shape=(), dtype=float32...   
17         0.984931  (tf.Tensor(0.59259254, shape=(), dtype=float32...   
18         0.985522  (tf.Tensor(0.6428571, shape=(), dtype=float32)...   
19         0.985493  (tf.Tensor(0.56, shape=(), dtype=float32), tf....   
20         0.985716  (tf.Tensor(0.6896551, shape=(), dtype=float32)...   
21         0.985445  (tf.Tensor(0.57142854, shape=(), dtype=float32...   
22         0.986027  (tf.Tensor(0.7142857, shape=(), dtype=float32)...   
23         0.986007  (tf.Tensor(0.6666667, shape=(), dtype=float32)...   
24         0.986094  (tf.Tensor(0.59259254, shape=(), dtype=float32...   
25         0.986540  (tf.Tensor(0.6896551, shape=(), dtype=float32)...   
26         0.986686  (tf.Tensor(0.6153846, shape=(), dtype=float32)...   
27         0.986977  (tf.Tensor(0.7741935, shape=(), dtype=float32)...   
28         0.986260  (tf.Tensor(0.7096774, shape=(), dtype=float32)...   
29         0.986143  (tf.Tensor(0.74999994, shape=(), dtype=float32...   
30         0.987413  (tf.Tensor(0.6896551, shape=(), dtype=float32)...   
31         0.986909  (tf.Tensor(0.59259254, shape=(), dtype=float32...   
32         0.983816  (tf.Tensor(0.17391302, shape=(), dtype=float32...   
33         0.991485  (tf.Tensor(0.56, shape=(), dtype=float32), tf....   
34         0.995461  (tf.Tensor(0.7741935, shape=(), dtype=float32)...   
35         0.997080  (tf.Tensor(0.88235295, shape=(), dtype=float32...   
36         0.997682  (tf.Tensor(0.91891885, shape=(), dtype=float32...   
37         0.998176  (tf.Tensor(0.9090909, shape=(), dtype=float32)...   
38         0.997972  (tf.Tensor(0.94444436, shape=(), dtype=float32...   
39         0.998661  (tf.Tensor(1.0, shape=(), dtype=float32), tf.T...   
40         0.998962  (tf.Tensor(1.0, shape=(), dtype=float32), tf.T...   
41         0.998817  (tf.Tensor(1.0, shape=(), dtype=float32), tf.T...   
42         0.999001  (tf.Tensor(1.0, shape=(), dtype=float32), tf.T...   
43         0.999369  (tf.Tensor(1.0, shape=(), dtype=float32), tf.T...   
44         0.998419  (tf.Tensor(0.9714285, shape=(), dtype=float32)...   
45         0.997730  (tf.Tensor(0.9714285, shape=(), dtype=float32)...   

    f1_score_weighted      loss  val_binary_accuracy  \
0            0.423447  0.103757             0.971573   
1            0.565585  0.071132             0.971806   
2            0.621689  0.062368             0.974214   
3            0.652763  0.057569             0.974835   
4            0.678149  0.054012             0.975612   
5            0.700567  0.051041             0.975456   
6            0.706454  0.050101             0.977010   
7            0.730846  0.047113             0.977243   
8            0.732256

***
***
***
***
***

# Test Data

##### Best Epoch Validation Metrics

In [21]:
df = combined_history[combined_history.val_loss == combined_history.val_loss.min()].reset_index(drop=True)
df["model"] = model.name

##### Model Test Metrics
- Load the model and get test set metrics
- Add the metrics to the dictionary for later analysis

In [22]:
test_model = keras.models.load_model(f"../saved_models/{model.name}.keras")

In [23]:
test_model.summary()

Model: "inceptionresnetv2_binary"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_layer_1 (InputLayer)      │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ true_divide (TrueDivide)        │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ subtract (Subtract)             │ (None, 299, 299, 3)    │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ inceptionresnetv2 (Functional)  │ (None, 8, 8, 1536)     │    54,336,736 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ sequential (Sequential)         │ (None, 1536)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 1536)           │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ classifier_layer (Dense)        │ (None, 25)             │        38,425 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 120,245,297 (458.70 MB)

 Trainable params: 32,935,065 (125.64 MB)

 Non-trainable params: 21,440,096 (81.79 MB)

 Optimizer params: 65,870,136 (251.27 MB)

In [24]:
print(test_model._compile_metrics.metrics)
test_loss, test_acc, test_f1_weighted, test_f1_per_class = test_model.evaluate(test_ds)

[]
33/33 ━━━━━━━━━━━━━━━━━━━━ 26s 411ms/step - binary_accuracy: 0.9852 - f1_score_per_class: 0.5771 - f1_score_weighted: 0.7994 - loss: 0.0529


In [25]:
df.loc[0,"test_loss"] = test_loss
test_acc_name = "test_binary_accuracy" if binary else "test_categorical_accuracy"
df.loc[0, test_acc_name] = test_acc
df.loc[0, "test_f1_score_weighted"] = test_f1_weighted
df["test_f1_score_per_class"] = [list(test_f1_per_class.numpy())]
df

binary_accuracy                                 f1_score_per_class  \
0          0.99708  (tf.Tensor(0.88235295, shape=(), dtype=float32...   

   f1_score_weighted      loss  val_binary_accuracy  \
0           0.964262  0.008328             0.986951   

                              val_f1_score_per_class  val_f1_score_weighted  \
0  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...                0.82015   

   val_loss type  epoch                     model  test_loss  \
0  0.038758   FT     35  inceptionresnetv2_binary   0.052088   

   test_binary_accuracy  test_f1_score_weighted  \
0              0.984747                0.796656   

                             test_f1_score_per_class  
0  [0.0, 0.36363626, 0.711111, 0.89908254, 0.7142...

In [37]:
csv_path = "../model_metrics/model_metrics_binary.csv" if binary else "../model_metrics/model_metrics.csv"

print(csv_path)
#df.to_csv(csv_path, index=False)
df_metrics = pd.read_csv(csv_path)
#df_metrics = pd.concat([df_metrics, df]).reset_index(drop=True)
df_metrics.sort_values(by="test_loss", ascending=True)
df_metrics.head()

../model_metrics/model_metrics_binary.csv


binary_accuracy                                 f1_score_per_class  \
0         0.986889  tf.Tensor(\n[0.51851845 0.62121207 0.69720095 ...   
1         0.992891  tf.Tensor(\n[0.30769226 0.7789473  0.8195121  ...   
2         0.996120  tf.Tensor(\n[0.7647058  0.87248313 0.9349397  ...   
3         0.997080  tf.Tensor(\n[0.88235295 0.85618716 0.9016786  ...   

   f1_score_weighted      loss  val_binary_accuracy  \
0           0.832202  0.033339             0.984758   
1           0.910056  0.019290             0.983236   
2           0.952604  0.011501             0.985892   
3           0.964262  0.008328             0.986951   

                              val_f1_score_per_class  val_f1_score_weighted  \
0  tf.Tensor(\n[0.         0.30769226 0.6956521  ...               0.765038   
1  tf.Tensor(\n[0.         0.5142857  0.7407407  ...               0.789391   
2  tf.Tensor(\n[0.         0.5714285  0.7826087  ...               0.806787   
3  tf.Tensor(\n[0.         0.53333324 0.74999994 ...               0.820150   

   val_loss type  epoch                     model  test_loss  \
0  0.045127   FT     12          mobilenet_binary   0.041557   
1  0.044372  CLF      4              vgg16_binary   0.049901   
2  0.047363   FT     22        inceptionv3_binary   0.044081   
3  0.038758   FT     35  inceptionresnetv2_binary   0.052088   

   test_binary_accuracy  test_f1_score_weighted  \
0              0.984844                0.774099   
1              0.983178                0.789475   
2              0.986667                0.809430   
3              0.984747                0.796656   

                             test_f1_score_per_class  
0  [0.0, 0.38461536, 0.5641025, 0.9115044, 0.4999...  
1  [0.0, 0.59459454, 0.6530612, 0.9107142, 0.2499...  
2  [0.0, 0.60606056, 0.6666666, 0.9209302, 0.7499...  
3  [0.0, 0.36363626, 0.711111, 0.89908254, 0.7142...

In [36]:
df_metrics.to_csv(csv_path, index=False)

***
***
***
***
***

# Softmax vs Binary
The following cells only run if filtered = True, if using the stratified/filtered dataset.  These are used to display the predicted vs true labels for both multi-class and multi-label classification methodologies, to demonstrate their difference in calculation methods.

In [ ]:
multi_df = test_df.copy()
multi_df["num_diseases"] = multi_df[class_names].sum(axis=1)
multi_df = multi_df[multi_df.num_diseases > 1]
multi_df

In [ ]:
multi_ds1 = dataset_from_dataframe(multi_df, class_names).shuffle(len(multi_df))
multi_ds1 = multi_ds1.map(lambda x,y:process_dataset(x, y, return_filenames=False))
print(f"MultiLabel Test Samples: {len(multi_df)}")
print()
for i in multi_ds1.element_spec:
    print(i)

for x, y in multi_ds1.take(1):
    print(x)
    print(y)

multi_ds1 = configure_dataset_for_performance(multi_ds1, shuffle=True)

In [ ]:
if filtered:
    model_binary = keras.models.load_model("../saved_models/mobilenet_binary.keras")
    img_dim = model_binary.input_shape[1]
    multi_ds = multi_ds1.map(lambda x,y: (apply_resize(x, img_dim), y), num_parallel_calls=AUTOTUNE)
        
    for img_batch, labels_batch in multi_ds:
        predict_proba = model_binary.predict(img_batch)
        print(predict_proba.shape)
        predictions = np.rint(predict_proba).astype(int)
        for i in range(len(predictions)):
            total_count += 1
            print("Predictions and Real Labels")
            print(predictions[i])
            print(labels_batch[i].numpy())
            equal = np.all(predictions[i] == labels_batch[i])
            print(equal)

else:
    print("Must use filtered dataset")

In [ ]:
if filtered:
    model_softmax = keras.models.load_model("../saved_models/mobilenet_softmax.keras")
    img_dim = model_softmax.input_shape[1]
    multi_ds = multi_ds1.map(lambda x,y: (apply_resize(x, img_dim), y), num_parallel_calls=AUTOTUNE)
    
    for img_batch, labels_batch in multi_ds:
        predict_proba = model_softmax.predict(img_batch)
        max_idx = np.argmax(predict_proba, axis=1)
        predict_proba2 = np.zeros(predict_proba.shape, dtype="int64")#
        for i in range(len(predict_proba2)):
            idx = max_idx[i]
            predict_samples = predict_proba2[i]
            predict_samples[idx] = 1
            print("Predictions and Labels")
            print(predict_samples)
            print(labels_batch[i].numpy())
            print()
else:
    print("Must use filtered dataset.")

***
***
***
***
***